# Movie Recommendations Capstone Project

## Introduction

We are given a dataset from Kaggle called [Movie Dataset](https://www.kaggle.com/datasets/rounakbanik/the-movies-dataset). This document contains 45,000 movies released on or before July 2017. Data points include cast, crew, plot keywords, budget, revenue, posters release dates language, production companies, contries, TMBD vote counts, and vote averages. 

The Movie Dataset has files containing 26 million ratings from 270,000 users for all 45,000 movies. Ratings are on a scale of 1-5.

Our goal for this project is to create a search engine where the user can search for keywords and our model will give recommendations based on the keywords

Steps:



*   Create dataframes for each CSV File and merger relevent features into one files
*   Exploratory Data Analysis on the dataframe created

*   Find and create target column
*   Build and test classifers






Team Members:



*   *Samuel Adeleye*
*   *Nasir Barnes*
*   *Jermaine Lennon*
*   *Antoine Teague*



## Creating DataFrames

### Installing Kaggle API

In [1]:
# Imports 
from google.colab import files
import zipfile
import os

In [2]:
!pip install -U -q kaggle
!mkdir  /root/.kaggle

# Upload kdggle.json api
files.upload()
!cp kaggle.json /root/.kaggle

mkdir: cannot create directory ‘/root/.kaggle’: File exists


Saving kaggle.json to kaggle (1).json


### Dowloading Data

In [3]:
# Downloading the dataset
!kaggle datasets download -d rounakbanik/the-movies-dataset

 94% 215M/228M [00:00<00:00, 286MB/s]
100% 228M/228M [00:00<00:00, 268MB/s]


In [4]:
!chmod 600 /root/.kaggle/kaggle.json

In [5]:
# This code allows us to unzip the file and remove it from this notebooks files
!apt install pv
!unzip -o /content/the-movies-dataset.zip  | pv -l >/dev/null


Reading package lists... Done
Building dependency tree       
Reading state information... Done
pv is already the newest version (1.6.6-1).
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 49 not upgraded.
8.00  0:00:08 [ 908m/s] [   <=>                                                ]


In [6]:
os.remove('the-movies-dataset.zip')

### DataFrames

In [7]:
# Imports
import pandas as pd


In [8]:
# In this code block we will create the dataframes for each file
credits_df = pd.read_csv('credits.csv', engine= 'python', encoding= 'utf-8', error_bad_lines= False)
movie_df = pd.read_csv('movies_metadata.csv')
keywords_df = pd.read_csv('keywords.csv')
links_df = pd.read_csv('links.csv')
links_small_df = pd.read_csv('links_small.csv') 
ratings_df = pd.read_csv('ratings.csv')
ratings_small_df = pd.read_csv('ratings_small.csv')

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2882: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version.


  exec(code_obj, self.user_global_ns, self.user_ns)
/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2882: DtypeWarning: Columns (10) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


## Exploratory Data Analysis

Checking and Modifying each dataset before merging into one Dataframe. This includes scanning each dataset for columns that have any missing data or mispelled labeling. The only dataframes we are looking at for this model are Credits, Keywords, and Movie Metadata. 


Project Notes: for Interactive  trained model

1.   Prompt user to pick one of the listed features
2.   prompt the user to typr in a name/datapoint within that feature 
3.   List the top most similar outputs(10 movie reccomendations)

- Keywords, credits, movie, Id
- The model should get a precise list of reccomendations by identifying movies by their ID in the dataframe.


### Movies Metadata Dataframe

#### Reviewing First Few Rows

In this section we want to look at the first few rows, drop the features not needed, and gain more insight on the data before we look at each column. 

In [9]:
movie_df.head(5)

adult                              belongs_to_collection    budget  \
0  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1  False                                                NaN  65000000   
2  False  {'id': 119050, 'name': 'Grumpy Old Men Collect...         0   
3  False                                                NaN  16000000   
4  False  {'id': 96871, 'name': 'Father of the Bride Col...         0   

                                              genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
1  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   
2  [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...   
3  [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   
4                     [{'id': 35, 'name': 'Comedy'}]   

                               homepage     id    imdb_id original_language  \
0  http://toystory.disney.com/toy-story    862  tt0114709                en   
1                                   NaN   8844  tt0113497                en   
2                                   NaN  15602  tt0113228                en   
3                                   NaN  31357  tt0114885                en   
4                                   NaN  11862  tt0113041                en   

                original_title  \
0                    Toy Story   
1                      Jumanji   
2             Grumpier Old Men   
3            Waiting to Exhale   
4  Father of the Bride Part II   

                                            overview  ... release_date  \
0  Led by Woody, Andy's toys live happily in his ...  ...   1995-10-30   
1  When siblings Judy and Peter discover an encha...  ...   1995-12-15   
2  A family wedding reignites the ancient feud be...  ...   1995-12-22   
3  Cheated on, mistreated and stepped on, the wom...  ...   1995-12-22   
4  Just when George Banks has recovered from his ...  ...   1995-02-10   

       revenue runtime                                   spoken_languages  \
0  373554033.0    81.0           [{'iso_639_1': 'en', 'name': 'English'}]   
1  262797249.0   104.0  [{'iso_639_1': 'en', 'name': 'English'}, {'iso...   
2          0.0   101.0           [{'iso_639_1': 'en', 'name': 'English'}]   
3   81452156.0   127.0           [{'iso_639_1': 'en', 'name': 'English'}]   
4   76578911.0   106.0           [{'iso_639_1': 'en', 'name': 'English'}]   

     status                                            tagline  \
0  Released                                                NaN   
1  Released          Roll the dice and unleash the excitement!   
2  Released  Still Yelling. Still Fighting. Still Ready for...   
3  Released  Friends are the people who let you be yourself...   
4  Released  Just When His World Is Back To Normal... He's ...   

                         title  video vote_average vote_count  
0                    Toy Story  False          7.7     5415.0  
1                      Jumanji  False          6.9     2413.0  
2             Grumpier Old Men  False          6.5       92.0  
3            Waiting to Exhale  False          6.1       34.0  
4  Father of the Bride Part II  False          5.7      173.0  

[5 rows x 24 columns]

Here we can see that there are 24 columns.

In [10]:
movie_df.columns

Index(['adult', 'belongs_to_collection', 'budget', 'genres', 'homepage', 'id',
       'imdb_id', 'original_language', 'original_title', 'overview',
       'popularity', 'poster_path', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'tagline', 'title', 'video',
       'vote_average', 'vote_count'],
      dtype='object')

In [11]:
movie_df.columns = ['Adult', 'Belongs to Collection', 'Budget', 'Genres', 'Home Page', 
                    'ID', 'IMDB ID', 'Original Language', 'Original Title',
                    'Overview', 'Popularity', 'Poster Path', 'Production Companies',
                    'Production Countries', 'Release Date', 'Revenue', 'Runtime'
                    'Spoken Languages', 'Status', 'Tagline', 'Title', 'Video', 
                    'Vote Average', 'Vote Count', '']

In [12]:
movie_df.columns

Index(['Adult', 'Belongs to Collection', 'Budget', 'Genres', 'Home Page', 'ID',
       'IMDB ID', 'Original Language', 'Original Title', 'Overview',
       'Popularity', 'Poster Path', 'Production Companies',
       'Production Countries', 'Release Date', 'Revenue',
       'RuntimeSpoken Languages', 'Status', 'Tagline', 'Title', 'Video',
       'Vote Average', 'Vote Count', ''],
      dtype='object')

Now that we changed the column names, we can drop the columns we don't need. For our model the only features we need are adult, genres, id, release data and title. 


In [13]:
movie_df = movie_df.drop(['Adult','Belongs to Collection', 'Budget', 'Home Page', 'IMDB ID', 
                          'Original Language',
                          'Popularity', 'Poster Path', 'Production Companies',
                          'Production Countries', 'Release Date', 'Revenue', 
                          'RuntimeSpoken Languages', 'Status', 'Tagline', 'Video',
                          'Vote Average', 'Vote Count', ''], axis=1)

In [14]:
movie_df.head(5)

Genres     ID  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...    862   
1  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   8844   
2  [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...  15602   
3  [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...  31357   
4                     [{'id': 35, 'name': 'Comedy'}]  11862   

                Original Title  \
0                    Toy Story   
1                      Jumanji   
2             Grumpier Old Men   
3            Waiting to Exhale   
4  Father of the Bride Part II   

                                            Overview  \
0  Led by Woody, Andy's toys live happily in his ...   
1  When siblings Judy and Peter discover an encha...   
2  A family wedding reignites the ancient feud be...   
3  Cheated on, mistreated and stepped on, the wom...   
4  Just when George Banks has recovered from his ...   

                                               Title  
0                                                NaN  
1          Roll the dice and unleash the excitement!  
2  Still Yelling. Still Fighting. Still Ready for...  
3  Friends are the people who let you be yourself...  
4  Just When His World Is Back To Normal... He's ...

From looking at the first few rows we can see that there is a lot of data in the dataframe. For this we want make sure there is no missing data but first we look at the types of data. 

In [15]:
movie_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45466 entries, 0 to 45465
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   Genres          45466 non-null  object
 1   ID              45466 non-null  object
 2   Original Title  45466 non-null  object
 3   Overview        44512 non-null  object
 4   Title           20412 non-null  object
dtypes: object(5)
memory usage: 1.7+ MB


In [16]:
movie_df.dtypes

Genres            object
ID                object
Original Title    object
Overview          object
Title             object
dtype: object

In [17]:
movie_df.describe()

Genres      ID Original Title  \
count                           45466   45466          45466   
unique                           4069   45436          43373   
top     [{'id': 18, 'name': 'Drama'}]  141971         Hamlet   
freq                             5000       3              8   

                  Overview                   Title  
count                44512                   20412  
unique               44307                   20283  
top     No overview found.  Based on a true story.  
freq                   133                       7

#### Genre Column

In [18]:
print(movie_df['Genres'].isna().any())

False


In [19]:
print(movie_df['Genres'].unique().shape)

(4069,)


In [20]:
for location in sorted(movie_df['Genres'].unique()):
  print(location)

[]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}, {'id': 10751, 'name': 'Family'}, {'id': 14, 'name': 'Fantasy'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}, {'id': 10751, 'name': 'Family'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}, {'id': 10752, 'name': 'War'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}, {'id': 14, 'name': 'Fantasy'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}, {'id': 18, 'name': 'Drama'}, {'id': 35, 'name': 'Comedy'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}, {'id': 18, 'name': 'Drama'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}, {'id': 35, 'name': 'Comedy'}, {'id': 18, 'name': 'Drama'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}, {'id': 35, 'name': 'Comedy'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10749, 'name': 'Romance'}]
[{'id': 10402, 'name': 'Music'}, {'id': 10751, 'name': 'Fam

In [21]:
movie_df['Genres'].value_counts()

[{'id': 18, 'name': 'Drama'}]                                                                                                         5000
[{'id': 35, 'name': 'Comedy'}]                                                                                                        3621
[{'id': 99, 'name': 'Documentary'}]                                                                                                   2723
[]                                                                                                                                    2442
[{'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}]                                                                       1301
                                                                                                                                      ... 
[{'id': 28, 'name': 'Action'}, {'id': 18, 'name': 'Drama'}, {'id': 35, 'name': 'Comedy'}, {'id': 99, 'name': 'Documentary'}]             1
[{'id': 10752, 'name': 'War

#### ID Column

In [22]:
print(movie_df['ID'].isna().any())

False


In [23]:
print(movie_df['ID'].unique().shape)

(45436,)


In [24]:
for location in sorted(movie_df['ID'].unique()):
  print(location)

Streaming output truncated to the last 5000 lines.
75840
75848
75861
75865
75874
75877
75878
75880
75886
75888
75889
75892
75896
75897
759
75900
75901
75903
75905
75910
75926
75931
75938
75944
75945
75947
75948
75950
75958
75963
75964
75969
75976
75981
75989
76
760
76000
76002
76010
76011
76012
76013
76018
76025
76040
76043
76047
76059
76076
76081
76083
76084
76094
76097
76099
761
76101
76102
76105
76112
76115
76116
76117
76121
76122
76127
76142
76155
76157
76162
76163
76164
76170
76171
76172
76176
76180
76198
76199
762
76200
76202
76203
76207
76211
76226
76229
76234
76235
76237
76264
76268
76277
76282
76285
76286
76287
76289
76297
763
76312
76323
76329
76330
76333
76338
76341
76344
76346
76348
76349
76350
76354
76360
76372
76380
76382
76395
76397
76399
764
76403
76406
76411
76420
76421
76422
76424
76438
76452
76464
76465
76468
76474
76475
76477
76483
76487
76489
76492
76493
76494
76498
76499
765
76516
76532
76533
76535
76543
76544
76547
76568
76575
76589
766
76600
76609
76617
76636
76

#### Title columns

##### Original Title

In [25]:
print(movie_df[ 'Original Title'].isna().any())

False


In [26]:
print(movie_df['Original Title'].unique().shape)

(43373,)


In [27]:
for location in sorted(movie_df['Original Title'].unique()):
  print(location)

Streaming output truncated to the last 5000 lines.
Vitus
Viudas
Viuuulentemente mia
Viva
Viva Cuba
Viva Knievel!
Viva Laldjerie
Viva Las Vegas
Viva Maria!
Viva Max!
Viva Riva!
Viva Villa!
Viva Zapata!
Viva l'Italia
Viva la libertà
Viva la muerte
Vivacious Lady
Vivat, Gardemariny!
Vive la France
Vivement dimanche!
Vivere
Vivi o, preferibilmente, morti
Vivien Leigh: Scarlett And Beyond
Vivir es Fácil con los Ojos Cerrados
Vivo per la tua morte
Vivre pour survivre
Vivre sa vie: film en douze tableaux
Vixen!
Viy
Vizi privati, pubbliche virtù
Vizontele
Vizontele Tuuba
Vlad
Vlad Tepes
Vladeniye 18
Voces inocentes
Voci nel tempo
Voditel dlya Very
Vodka Lemon
Vodkaa, komisario Palmu
Vogelfrei
Vogliamo i colonnelli
Voice from the Stone
Voice of the Whistler
Voices
Voices from the List
Voices of Iraq
Voici le temps des assassins...
Voir du pays
Voksne mennesker
Volcano
Voll Normaaal
Vollidiot
Volshebnaya Lampa Aladdina
Volunteers
Volver
Volver a empezar
Von Caligari zu Hitler: Das deutsche Kino 

##### Title

In [28]:
print(movie_df[ 'Title'].isna().any())

True


We will combine the two title columns so that there is no missing data. 

In [29]:
movie_df['Title'] = movie_df['Original Title']


In [30]:
print(movie_df[ 'Title'].isna().any())

False


In [31]:
print(movie_df['Title'].unique().shape)

(43373,)


In [32]:
for location in sorted(movie_df['Title'].unique()):
  print(location)

Streaming output truncated to the last 5000 lines.
Vitus
Viudas
Viuuulentemente mia
Viva
Viva Cuba
Viva Knievel!
Viva Laldjerie
Viva Las Vegas
Viva Maria!
Viva Max!
Viva Riva!
Viva Villa!
Viva Zapata!
Viva l'Italia
Viva la libertà
Viva la muerte
Vivacious Lady
Vivat, Gardemariny!
Vive la France
Vivement dimanche!
Vivere
Vivi o, preferibilmente, morti
Vivien Leigh: Scarlett And Beyond
Vivir es Fácil con los Ojos Cerrados
Vivo per la tua morte
Vivre pour survivre
Vivre sa vie: film en douze tableaux
Vixen!
Viy
Vizi privati, pubbliche virtù
Vizontele
Vizontele Tuuba
Vlad
Vlad Tepes
Vladeniye 18
Voces inocentes
Voci nel tempo
Voditel dlya Very
Vodka Lemon
Vodkaa, komisario Palmu
Vogelfrei
Vogliamo i colonnelli
Voice from the Stone
Voice of the Whistler
Voices
Voices from the List
Voices of Iraq
Voici le temps des assassins...
Voir du pays
Voksne mennesker
Volcano
Voll Normaaal
Vollidiot
Volshebnaya Lampa Aladdina
Volunteers
Volver
Volver a empezar
Von Caligari zu Hitler: Das deutsche Kino 

#### Overview

In [33]:
print(movie_df['Overview'].isna().any())

True


In [34]:
print(movie_df['Overview'].unique().shape)

(44308,)


### Credits Dataframe

#### Reviewing First Few Rows

Like the 'Movies Metadata Dataframe' we are going to stat be looking at the first few rows. 

In [35]:
credits_df.head(5)

cast  \
0  [{'cast_id': 14, 'character': 'Woody (voice)',...   
1  [{'cast_id': 1, 'character': 'Alan Parrish', '...   
2  [{'cast_id': 2, 'character': 'Max Goldman', 'c...   
3  [{'cast_id': 1, 'character': "Savannah 'Vannah...   
4  [{'cast_id': 1, 'character': 'George Banks', '...   

                                                crew     id  
0  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...    862  
1  [{'credit_id': '52fe44bfc3a36847f80a7cd1', 'de...   8844  
2  [{'credit_id': '52fe466a9251416c75077a89', 'de...  15602  
3  [{'credit_id': '52fe44779251416c91011acb', 'de...  31357  
4  [{'credit_id': '52fe44959251416c75039ed7', 'de...  11862

We see that there is three columns. 

In [36]:
credits_df.columns

Index(['cast', 'crew', 'id'], dtype='object')

In [37]:
credits_df.columns = ['Cast', 'Crew', 'ID']

In [38]:
credits_df.columns

Index(['Cast', 'Crew', 'ID'], dtype='object')

In [39]:
credits_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45476 entries, 0 to 45475
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   Cast    45476 non-null  object
 1   Crew    45476 non-null  object
 2   ID      45476 non-null  int64 
dtypes: int64(1), object(2)
memory usage: 1.0+ MB


In [40]:
credits_df.dtypes

Cast    object
Crew    object
ID       int64
dtype: object

In [41]:
credits_df.describe()

ID
count   45476.000000
mean   108345.997537
std    112443.796536
min         2.000000
25%     26443.250000
50%     60002.500000
75%    157302.000000
max    469172.000000

#### Cast Column

First we going to look at the cast column. Is there any missing data?

In [42]:
print(credits_df['Cast'].isna().any())

False


We see that there is no missing data, so lets see the unique shapes

In [43]:
print(credits_df['Cast'].unique().shape)

(43019,)


In [44]:
for location in sorted(credits_df['Cast'].unique()):
  print(location)

[]
[{'cast_id': 0, 'character': "''Connasse''", 'credit_id': '54e32c8fc3a36823d4000907', 'gender': 0, 'id': 1348474, 'name': 'Camille Cottin', 'order': 1, 'profile_path': '/zgiFZTW44dQxBl0pekbAf4J3Vm7.jpg'}, {'cast_id': 3, 'character': 'William (voice)', 'credit_id': '5633458192514129fe007630', 'gender': 2, 'id': 582673, 'name': 'Antony Hickling', 'order': 2, 'profile_path': '/aZTKFFhHpSfXmji8cbCw7Sun4k4.jpg'}, {'cast_id': 4, 'character': 'Camille enfant #1', 'credit_id': '5633458a9251416d52006f6f', 'gender': 0, 'id': 1529254, 'name': 'Lou Cottin', 'order': 3, 'profile_path': None}, {'cast_id': 5, 'character': 'La nanny', 'credit_id': '563345a1c3a3681b4b013a69', 'gender': 1, 'id': 1097144, 'name': 'Cécile Boland', 'order': 4, 'profile_path': '/NoUqjuFd4KA4RUYknFh4XcKmxz.jpg'}, {'cast_id': 10, 'character': 'Lui même', 'credit_id': '5667f565c3a36836af0022fe', 'gender': 0, 'id': 1253585, 'name': 'Stéphane Bern', 'order': 5, 'profile_path': '/njvNjX55sZ20zHLXSMnQSfwYRRg.jpg'}]
[{'cast_id':

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



#### Crew Column

In [45]:
print(credits_df['Crew'].isna().any())

False


In [46]:
print(credits_df['Crew'].unique().shape)

(44669,)


In [47]:
for location in sorted(credits_df['Crew'].unique()):
  print(location)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[{'credit_id': '52fe468bc3a36847f8104d4f', 'department': 'Production', 'gender': 2, 'id': 280, 'job': 'Executive Producer', 'name': 'Terry Gilliam', 'profile_path': '/cFno5isSPvfPEkSdVoEzOs0pJCh.jpg'}, {'credit_id': '577ed19f9251416c43001316', 'department': 'Production', 'gender': 0, 'id': 19748, 'job': 'Associate Producer', 'name': 'Michael Becker', 'profile_path': None}, {'credit_id': '577ed1c792514132970056e5', 'department': 'Production', 'gender': 0, 'id': 36645, 'job': 'Co-Producer', 'name': 'Jörg Rothe', 'profile_path': None}, {'credit_id': '577ed1c0925141697600432d', 'department': 'Production', 'gender': 0, 'id': 36646, 'job': 'Producer', 'name': 'Alexander Ris', 'profile_path': None}, {'credit_id': '577ed1b9c3a3684926001681', 'department': 'Production', 'gender': 0, 'id': 55486, 'job': 'Producer', 'name': 'Hengameh Panahi', 'profile_path': None}, {'credit_id': '577ed1cfc3a3686a09003129', 'department': 'Production', 'gender': 2, 'id': 55418, 'job': 'Executive Producer', 'name': 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[{'credit_id': '59cdd09ec3a3686aa90094f9', 'department': 'Art', 'gender': 2, 'id': 10604, 'job': 'Art Direction', 'name': 'George W. Davis', 'profile_path': None}, {'credit_id': '59cdd085c3a3686abc009026', 'department': 'Camera', 'gender': 2, 'id': 96427, 'job': 'Director of Photography', 'name': 'Paul Vogel', 'profile_path': None}, {'credit_id': '59cdd0959251416c20009a1b', 'department': 'Editing', 'gender': 2, 'id': 22599, 'job': 'Editor', 'name': 'Ben Lewis', 'profile_path': None}, {'credit_id': '59cdd06e9251416c43009773', 'department': 'Production', 'gender': 2, 'id': 34112, 'job': 'Producer', 'name': 'Sam Katzman', 'profile_path': None}, {'credit_id': '52fe491a9251416c750bd8b5', 'department': 'Writing', 'gender': 2, 'id': 103355, 'job': 'Screenplay', 'name': 'Orville H. Hampton', 'profile_path': None}, {'credit_id': '59cdd0a9c3a3686a9200880d', 'department': 'Art', 'gender': 2, 'id': 552346, 'job': 'Art Direction', 'name': 'Merrill Pye', 'profile_path': '/mSXc4DfbM3iuwqmoQtEgOkTFoA5

#### ID Column

In [48]:
print(credits_df['ID'].isna().any())

False


In [49]:
print(credits_df['ID'].unique().shape)

(45432,)


In [50]:
for location in sorted(credits_df['ID'].unique()):
  print(location)

Streaming output truncated to the last 5000 lines.
289225
289232
289239
289269
289278
289314
289318
289333
289336
289339
289390
289394
289416
289510
289519
289520
289523
289575
289673
289679
289712
289716
289720
289723
289727
289728
289781
289820
289891
289923
289933
289960
290043
290075
290098
290100
290157
290188
290217
290235
290250
290274
290283
290290
290300
290304
290316
290365
290370
290379
290382
290504
290542
290555
290556
290595
290637
290656
290672
290695
290714
290727
290729
290739
290751
290762
290764
290773
290789
290802
290815
290825
290862
290864
290865
290911
290916
290930
290999
291006
291122
291146
291151
291154
291155
291156
291157
291162
291164
291189
291224
291264
291270
291272
291276
291290
291325
291328
291336
291343
291348
291351
291356
291362
291375
291413
291495
291537
291540
291549
291554
291558
291577
291613
291634
291675
291680
291692
291731
291805
291817
291851
291854
291861
291863
291865
291866
291868
291869
291870
291871
291907
291976
292010
292014
2920

### Keywords

The last feature we need for our model is 'Keywords.' So lets make sure that there is no missing data. 

#### Reviewing First Few Rows

In this section we want to look at the first few rows, drop the features not needed, and gain more insight on the data before we look at each column. 

In [51]:
keywords_df.head(5)

id                                           keywords
0    862  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...
1   8844  [{'id': 10090, 'name': 'board game'}, {'id': 1...
2  15602  [{'id': 1495, 'name': 'fishing'}, {'id': 12392...
3  31357  [{'id': 818, 'name': 'based on novel'}, {'id':...
4  11862  [{'id': 1009, 'name': 'baby'}, {'id': 1599, 'n...

Here we can see that there are 24 columns.

In [52]:
keywords_df.columns

Index(['id', 'keywords'], dtype='object')

In [53]:
keywords_df.columns = ['ID', 'Keywords']

In [54]:
keywords_df.columns

Index(['ID', 'Keywords'], dtype='object')

In [55]:
keywords_df.dtypes

ID           int64
Keywords    object
dtype: object

In [56]:
keywords_df

ID                                           Keywords
0         862  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...
1        8844  [{'id': 10090, 'name': 'board game'}, {'id': 1...
2       15602  [{'id': 1495, 'name': 'fishing'}, {'id': 12392...
3       31357  [{'id': 818, 'name': 'based on novel'}, {'id':...
4       11862  [{'id': 1009, 'name': 'baby'}, {'id': 1599, 'n...
...       ...                                                ...
46414  439050             [{'id': 10703, 'name': 'tragic love'}]
46415  111109  [{'id': 2679, 'name': 'artist'}, {'id': 14531,...
46416   67758                                                 []
46417  227506                                                 []
46418  461257                                                 []

[46419 rows x 2 columns]

#### Keywords Column

In [57]:
print(keywords_df['Keywords'].isna().any())

False


No missing data here. Lets see the amount of shapes in the feature

In [58]:
print(keywords_df['Keywords'].unique().shape)

(25989,)


In [59]:
for location in sorted(keywords_df['Keywords'].unique()):
  print(location)

Streaming output truncated to the last 5000 lines.
[{'id': 1909, 'name': 'coffin'}, {'id': 2551, 'name': 'pet'}, {'id': 3739, 'name': 'funeral'}, {'id': 6350, 'name': 'head injury'}, {'id': 9872, 'name': 'grief'}, {'id': 14819, 'name': 'violence'}, {'id': 18127, 'name': 'new neighbor'}, {'id': 157488, 'name': 'pet cemetery'}, {'id': 157490, 'name': 'dead cat'}, {'id': 157492, 'name': 'death of patient'}, {'id': 157495, 'name': 'loss of pet'}, {'id': 157496, 'name': 'dead lover'}, {'id': 157499, 'name': 'mother son relationship'}, {'id': 162846, 'name': 'ghost'}, {'id': 171247, 'name': 'grave robbing'}, {'id': 173099, 'name': 'indian burial ground'}, {'id': 187056, 'name': 'woman director'}, {'id': 187844, 'name': 'flashback'}, {'id': 192865, 'name': 'burial ground'}]
[{'id': 1909, 'name': 'coffin'}, {'id': 2708, 'name': 'hitman'}, {'id': 3568, 'name': 'lone wolf'}, {'id': 5692, 'name': 'stetson'}, {'id': 156212, 'name': 'spaghetti western'}, {'id': 160324, 'name': 'django'}]
[{'id': 19

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[{'id': 9714, 'name': 'remake'}, {'id': 10292, 'name': 'gore'}, {'id': 161663, 'name': 'street children'}, {'id': 177201, 'name': 'evil child'}, {'id': 194310, 'name': 'killer children'}, {'id': 194311, 'name': 'mexican island'}]
[{'id': 9714, 'name': 'remake'}, {'id': 10388, 'name': 'lord'}]
[{'id': 9714, 'name': 'remake'}, {'id': 10562, 'name': 'on the run'}, {'id': 15363, 'name': 'bank robbery'}, {'id': 207446, 'name': 'comedy of errors'}]
[{'id': 9714, 'name': 'remake'}, {'id': 10563, 'name': 'attack'}, {'id': 12377, 'name': 'zombie'}, {'id': 12394, 'name': 'chainsaw'}]
[{'id': 9714, 'name': 'remake'}, {'id': 10770, 'name': 'mad doctor'}, {'id': 15071, 'name': 'centenarian'}, {'id': 33498, 'name': 'transplant'}, {'id': 155730, 'name': 'hammer horror'}, {'id': 206091, 'name': 'adrenal gland'}]
[{'id': 9714, 'name': 'remake'}, {'id': 12377, 'name': 'zombie'}, {'id': 14909, 'name': 'alien invasion'}]
[{'id': 9714, 'name': 'remake'}, {'id': 12425, 'name': 'racism'}]
[{'id': 9714, 'name

In [60]:
keywords_df.head(10)

ID                                           Keywords
0    862  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...
1   8844  [{'id': 10090, 'name': 'board game'}, {'id': 1...
2  15602  [{'id': 1495, 'name': 'fishing'}, {'id': 12392...
3  31357  [{'id': 818, 'name': 'based on novel'}, {'id':...
4  11862  [{'id': 1009, 'name': 'baby'}, {'id': 1599, 'n...
5    949  [{'id': 642, 'name': 'robbery'}, {'id': 703, '...
6  11860  [{'id': 90, 'name': 'paris'}, {'id': 380, 'nam...
7  45325                                                 []
8   9091  [{'id': 949, 'name': 'terrorist'}, {'id': 1562...
9    710  [{'id': 701, 'name': 'cuba'}, {'id': 769, 'nam...

## Preprocessing

### Merging Dataframes


In this section we are going to merge the features we need into one dataframe. 

#### Movie Meta DataFrame

In [61]:
import pandas as pd

In [62]:
movies = pd.DataFrame()

In [63]:
movies['ID'] = movie_df['ID']

In [64]:
movies['Title'] = movie_df['Title']

In [65]:
movies['Original Title'] = movie_df['Original Title']

In [66]:
movies['Overview'] = movie_df['Overview']

In [67]:
movies['Genres'] = movie_df['Genres']

In [68]:
movies.head(1)

ID      Title Original Title  \
0  862  Toy Story      Toy Story   

                                            Overview  \
0  Led by Woody, Andy's toys live happily in his ...   

                                              Genres  
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...

#### Keywords

In [69]:
movies['Keywords'] = keywords_df['Keywords']

In [70]:
movies.head(1)

ID      Title Original Title  \
0  862  Toy Story      Toy Story   

                                            Overview  \
0  Led by Woody, Andy's toys live happily in his ...   

                                              Genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   

                                            Keywords  
0  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...

#### Cast

In [71]:
movies['Cast'] = credits_df['Cast']

In [72]:
movies.head(1)

ID      Title Original Title  \
0  862  Toy Story      Toy Story   

                                            Overview  \
0  Led by Woody, Andy's toys live happily in his ...   

                                              Genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   

                                            Keywords  \
0  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...   

                                                Cast  
0  [{'cast_id': 14, 'character': 'Woody (voice)',...

#### Dropping Data That Out of Place

In [73]:
#This movie has no ID 
movie_df  = movie_df.drop(29503)

In [74]:
#This movie has no ID 

movie_df  = movie_df.drop(35587)

In [75]:
#This movie has no ID 

movie_df  = movie_df.drop(19730)

### Modifying Columns

In [76]:
movies['Genre'] = movies['Genres'].apply(lambda x: [i['name'] for i in eval(x)])
movies['Genre'] = movies['Genre'].apply(lambda x: [i.replace(" ", "") for i in x])
movies['Genre'] = movies['Genre'].apply(lambda x: ' '.join(x))


In [77]:
movies.drop('Genres', axis=1, inplace=True)


In [78]:
movies['Cast'] = movies['Cast'].apply(lambda x: [i['name'] for i in eval(x)])
movies['Cast'] = movies['Cast'].apply(lambda x: ' '.join([i.replace(" ", "") for i in x]))


In [79]:
movies['Keywords'] = movies['Keywords'].apply(lambda x: [i['name'] for i in eval(x)])
movies['Keywords'] = movies['Keywords'].apply(lambda x: ' '.join([i.replace(" ", "") for i in x]))

In [80]:
movies.head(5)

ID                        Title               Original Title  \
0    862                    Toy Story                    Toy Story   
1   8844                      Jumanji                      Jumanji   
2  15602             Grumpier Old Men             Grumpier Old Men   
3  31357            Waiting to Exhale            Waiting to Exhale   
4  11862  Father of the Bride Part II  Father of the Bride Part II   

                                            Overview  \
0  Led by Woody, Andy's toys live happily in his ...   
1  When siblings Judy and Peter discover an encha...   
2  A family wedding reignites the ancient feud be...   
3  Cheated on, mistreated and stepped on, the wom...   
4  Just when George Banks has recovered from his ...   

                                            Keywords  \
0  jealousy toy boy friendship friends rivalry bo...   
1  boardgame disappearance basedonchildren'sbook ...   
2     fishing bestfriend duringcreditsstinger oldmen   
3  basedonnovel interracialrelationship singlemot...   
4  baby midlifecrisis confidence aging daughter m...   

                                                Cast                     Genre  
0  TomHanks TimAllen DonRickles JimVarney Wallace...   Animation Comedy Family  
1  RobinWilliams JonathanHyde KirstenDunst Bradle...  Adventure Fantasy Family  
2  WalterMatthau JackLemmon Ann-Margret SophiaLor...            Romance Comedy  
3  WhitneyHouston AngelaBassett LorettaDevine Lel...      Comedy Drama Romance  
4  SteveMartin DianeKeaton MartinShort KimberlyWi...                    Comedy

### Tags

Creating a tags column which will include: Original Title, Overview, Keywords, Cast, Genre. 

First we will make another dataframe. 

In [81]:
import pandas as pd


In [82]:
movie = pd.DataFrame()

In [83]:
movie['ID'] = movies['ID']

In [84]:
movie['Title'] = movies['Title']

In [85]:
movie['Tags'] = movies['Overview']+' '+movies['Keywords']+' '+movies['Cast']+' '+movies['Genre']+' '+movies['Title']

In [86]:
movie.head(5)

ID                        Title  \
0    862                    Toy Story   
1   8844                      Jumanji   
2  15602             Grumpier Old Men   
3  31357            Waiting to Exhale   
4  11862  Father of the Bride Part II   

                                                Tags  
0  Led by Woody, Andy's toys live happily in his ...  
1  When siblings Judy and Peter discover an encha...  
2  A family wedding reignites the ancient feud be...  
3  Cheated on, mistreated and stepped on, the wom...  
4  Just when George Banks has recovered from his ...

In [87]:
movie.describe()

ID   Title                                               Tags
count    45466   45466                                              44512
unique   45436   43373                                              44504
top     141971  Hamlet  Recovering from a nail gun shot to the head an...
freq         3       8                                                  3

In [88]:
movie.isnull().sum()


ID         0
Title      0
Tags     954
dtype: int64

In [89]:
movie.drop(movie[movie['Tags'].isnull()].index, inplace=True)
movie.drop_duplicates(inplace=True)


In [90]:
movie.isnull().sum()


ID       0
Title    0
Tags     0
dtype: int64

In [91]:
movie.shape

(44504, 3)

## Vectorizing Data

In this section we will perform a technique called [Vectorizing Data](https://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.TfidfVectorizer.html) which is used to speed up Python code. 

In [92]:
import sklearn
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD


In [93]:
Vectorizer = TfidfVectorizer(max_features=5000)
svd = TruncatedSVD(n_components=3000)


In [94]:
vectorized_data = Vectorizer.fit_transform(movie['Tags'].values)


In [95]:
vectorized_dataframe = pd.DataFrame(vectorized_data.toarray(), index=movie['Tags'].index.tolist())


In [96]:
#reduced_data = svd.fit_transform(vectorized_dataframe)


In [96]:
from sklearn.metrics.pairwise import cosine_similarity


In [ ]:
similarity = cosine_similarity(vectorized_dataframe)


In [ ]:
def recommendation(movie_title):
    id_of_movie = movie[movie['Title']==movie_title].index[0]
    distances = similarity[id_of_movie]
    movie_list = sorted(list(enumerate(distances)), reverse=True, key=lambda x:x[1])[1:10]
    
    for i in movie_list:
        print(movie.iloc[i[0]].title)

## Prompting the user

Using input functions to prompt the user for a feature and a sspecific data point for a list of 10 reccommended movies from the modified Dataframe using cosine similarity.(Numeric Quantity)

In [ ]:
feature_select = input("Choose a movie feature: keywords, genre, title or release date: ")



Choose a movie feature: keywords, genre, title or release date: 2001
